# Visualizing Methane Plume Timeseries

**Summary**  

In this notebook, we'll conduct a search and visualize the available methane plume complex observations detected by the Earth Mineral Dust Source Investigation (EMIT) instrument, then select a region of interest (ROI) that shows several plumes that appear to be from the same source. We will then visualize a time series of plume data for the ROI, calculate the integrated methane enhancement, or mass of methane observed in each plume. Lastly, to add more context to the plume timeseries, we will look at all EMIT observations over the target regions and determine if there were factors such as clouds limiting plume detection, or simply no methane emissions during additional overpasses.

> Throughout this notebook, several complex functions and workflows are used to process and visualize data. These can be found in the `emit_tools.py` and `tutorial_utils.py` modules.

**Background**

Methane is major contributor to atmospheric radiative forcing because its more efficient at trapping radiation than other greenhouse gases, like carbon dioxide. Because the lifetime of methane in the atmosphere is only about 10 years, reducing methane emissions offers an effective way to curb anthropogenic contributions to atmospheric radiative forcing.

The EMIT instrument is an imaging spectrometer that measures light in visible and infrared wavelengths. These measurements display unique spectral signatures that correspond to chemical composition. Although the primary mission focuses on mapping the mineral composition of Earth's surface, the EMIT instrument has also been used to successfully map methane point source emissions within its target mask using the unique spectral fingerprint of methane. More details about EMIT and its associated products can be found in the **README.md** and on the [EMIT website](https://earth.jpl.nasa.gov/emit/).

The L2B Estimated Methane Plume Complexes ([EMITL2BCH4PLM](https://lpdaac.usgs.gov/products/emitl2bch4plmv001/)) product provides delineated methane plume complexes in parts per million meter (ppm m) along with associated uncertainties. This product is a plume specific subset of the EMIT L2B Methane Enhancement Data ([EMITL2BCH4ENH](https://lpdaac.usgs.gov/products/emitl2bch4enhv001/)) product. Each EMITL2BCH4PLM granule is sized to a specific plume complex but may cross multiple EMITL2BCH4ENH granules. A list of source EMITL2BCH4ENH granules is included in the GeoTIFF file metadata as well as the GeoJSON file. Each EMITL2BCH4PLM granule contains two files: one Cloud Optimized GeoTIFF (COG) file at a spatial resolution of 60 meters (m) and one GeoJSON file. The EMITL2BCH4PLM COG file contains a raster image of a methane plume complex extracted from EMITL2BCH4ENH v001 data. The EMITL2BCH4PLM GeoJSON file contains a vector outline of the plume complex, a list of source scenes, coordinates of the maximum enhancement values with associated uncertainties. 

The EMITL2BCH4ENH product only includes granules where methane plume complexes have been identified. To reduce the risk of false positives, all EMITL2BCH4ENH data undergo a manual review (or identification and confirmation) process before being designated as a plume complex. For more information on the manual review process, see Section 4.2.2 of the [EMIT GHG Algorithm Theoretical Basis Document (ATBD)](https://lpdaac.usgs.gov/documents/1696/EMIT_GHG_ATBD_V1.pdf). 


**References**

Andrew K. Thorpe et al., Attribution of individual methane and carbon dioxide emission sources using EMIT observations from space. Sci. Adv.9, eadh2391 (2023). DOI:[10.1126/sciadv.adh2391](https://www.science.org/doi/10.1126/sciadv.adh2391)

**Requirements** 
 - Set up Python Environment - See **setup_instructions.md** in the `/setup/` folder
 - NASA Earthdata Login Account. [Sign Up](https://urs.earthdata.nasa.gov/users/new)

**Data Used** 
 - [EMIT L2B Estimated Methane Plume Complexes (EMITL2BCH4PLM)](https://lpdaac.usgs.gov/products/emitl2bch4plmv001/)
 - [EMIT L2A Estimated Surface Reflectance and Uncertainty and Masks (EMITL2ARFL)](https://lpdaac.usgs.gov/products/emitl2arflv001/)

**Learning Objectives** 
 - Search for EMIT L2B Estimated Methane Plume Complexes
 - Visualize search results on a map
 - Retrieve and visualize the EMIT L2B Estimated Methane Plume Complexes Metadata
 - Select a region of interest and build a timeseries of plume data
 - Further investigate plume detection by looking at browse images and quality information

**Tutorial Outline**  

1. [**Setup**](#setup)
2. [**Search for EMIT L2B Estimated Methane Plume Complexes**](#search)
3. [**Creating a Timeseries from Plume Data**](#plume-timeseries)
4. [**Further investigation into plume detection**](#plume-detection)
5. [**Calculating the Integrated Methane Enhancement for Plumes**](#ime)

## 1. Set up<a id='setup'></a>

Import the necessary Python libraries.

In [1]:
# Import required libraries
import sys
import os
import glob
import requests
import numpy as np
import pandas as pd
import xarray as xr
from osgeo import gdal
import geopandas as gpd

from datetime import datetime
import folium
import earthaccess
import folium.plugins
import rioxarray as rxr

import hvplot.xarray
import hvplot.pandas

from branca.element import Figure
from IPython.display import display
from shapely.geometry.polygon import orient
from shapely.geometry import Point

sys.path.append('../modules/')
from emit_tools import emit_xarray, ortho_xr, ortho_browse
from tutorial_utils import list_metadata_fields, results_to_geopandas, convert_bounds

All of the data we use or save will go into the `methane_tutorial` directory, so we can go ahead and define that filepath now, relative to this notebook.

In [2]:
methane_dir = '../../data/methane_tutorial/'

## 2. Search for EMIT L2B Estimated Methane Plume Complexes<a id='search'></a>

Use `earthaccess` to find all EMIT L2B Estimated Methane Plume Complexes (EMITL2BCH4PLM) data available from 2023. Define the date range, and concept-ids (unique product identifier) for the EMIT products that we want to search for, but leave the spatial arguments like `polygon` and `bbox` empty so we can preview detected methane plumes globally. 

In [3]:
# Data Collections for our search, using a dictionary
concept_ids = {'plumes':'C2748088093-LPCLOUD', 'reflectance':'C2408750690-LPCLOUD'}
# Define Date Range
date_range = ('2023-01-01','2023-12-31')

In [4]:
results = earthaccess.search_data(
    concept_id=concept_ids['plumes'],
    temporal=date_range,
    count=2000
)

Granules found: 947


Convert the results to a `geopandas.GeoDataFrame` using a function from our `tutorial_utils` module. This gives a nice way to organize and visualize the search results.

In [5]:
gdf = results_to_geopandas(results)
gdf

size                                   native-id provider-id  \
0    0.012831  EMIT_L2B_CH4PLM_001_20230107T143818_000574     LPCLOUD   
1    0.034487  EMIT_L2B_CH4PLM_001_20230111T130107_000576     LPCLOUD   
2    0.005418  EMIT_L2B_CH4PLM_001_20230111T130218_000575     LPCLOUD   
3    0.007916  EMIT_L2B_CH4PLM_001_20230119T040223_000579     LPCLOUD   
4    0.015472  EMIT_L2B_CH4PLM_001_20230119T040223_000578     LPCLOUD   
..        ...                                         ...         ...   
942  0.022200  EMIT_L2B_CH4PLM_001_20231226T065450_002302     LPCLOUD   
943  0.020020  EMIT_L2B_CH4PLM_001_20231226T065514_002303     LPCLOUD   
944  0.070825  EMIT_L2B_CH4PLM_001_20231226T082757_002299     LPCLOUD   
945  0.134440  EMIT_L2B_CH4PLM_001_20231226T082757_002298     LPCLOUD   
946  0.274856  EMIT_L2B_CH4PLM_001_20231226T180707_002296     LPCLOUD   

        _single_date_time                                      _related_urls  \
0    2023-01-07T14:38:18Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
1    2023-01-11T13:01:07Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
2    2023-01-11T13:02:18Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
3    2023-01-19T04:02:23Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
4    2023-01-19T04:02:23Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
..                    ...                                                ...   
942  2023-12-26T06:54:50Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
943  2023-12-26T06:55:14Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
944  2023-12-26T08:27:57Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
945  2023-12-26T08:27:57Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
946  2023-12-26T18:07:07Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   

                                              geometry  
0    POLYGON ((-70.71011 -34.22767, -70.71390 -34.2...  
1    POLYGON ((-70.77084 -32.93065, -70.78006 -32.9...  
2    POLYGON ((-67.07444 -36.36352, -67.07607 -36.3...  
3    POLYGON ((148.68964 -22.97526, 148.68476 -22.9...  
4    POLYGON ((148.56059 -22.97038, 148.55517 -22.9...  
..                                                 ...  
942  POLYGON ((51.55031 30.09304, 51.54706 30.09141...  
943  POLYGON ((52.71774 29.43314, 52.70364 29.43206...  
944  POLYGON ((28.54772 29.55731, 28.54447 29.55569...  
945  POLYGON ((28.61713 29.60774, 28.61333 29.60069...  
946  POLYGON ((-58.76201 -34.51451, -58.76418 -34.5...  

[947 rows x 6 columns]

In [ ]:
gdf.to_csv("plumes.csv")

By default this function includes some fields, but you can add fields with a `fields` argument. To see all of the metadata available use the `list_metadata_fields` function imported from the `tutorial_utils.py` module.

In [6]:
list_metadata_fields(results)

['size',
 'concept-type',
 'concept-id',
 'revision-id',
 'native-id',
 'provider-id',
 'format',
 'revision-date',
 '_single_date_time',
 '_granule_ur',
 '_additional_attributes',
 '_gpolygons',
 '_provider_dates',
 '_short_name',
 '_version',
 '_pgename',
 '_pgeversion',
 '_related_urls',
 '_cloud_cover',
 '_day_night_flag',
 '_archive_and_distribution_information',
 '_production_date_time',
 '_platforms',
 '_url',
 '_name',
 '_version']

Add an index column to the dataframe to include it in the tooltips for our visualization.

In [7]:
# Specify index so we can reference it with gdf.explore()
gdf['index']=gdf.index

In [8]:
# Set up Figure and Basemap tiles
fig = Figure(width="1080px",height="540")
map1 = folium.Map(tiles=None)
folium.TileLayer(tiles='https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}',name='Google Satellite', attr='Google', overlay=True).add_to(map1)
folium.TileLayer(tiles='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}.png',
                name='ESRI World Imagery',
                attr='Tiles &copy; Esri &mdash; Source: Esri, i-cubed, USDA, USGS, AEX, GeoEye, Getmapping, Aerogrid, IGN, IGP, UPR-EGP, and the GIS User Community',
                overlay='True').add_to(map1)
fig.add_child(map1)
# Add Search Results gdf
gdf.explore("_single_date_time",
            categorical=True,
            style_kwds={"fillOpacity":0.1,"width":2},
            name="EMIT L2B CH4PLM",
            tooltip=[
                "index",
                "native-id",
                "_single_date_time",
            ],
            m=map1,
            legend=False
)

# Zoom to Data
map1.fit_bounds(bounds=convert_bounds(gdf.unary_union.bounds))
# Add Layer controls
map1.add_child(folium.LayerControl(collapsed=False))
display(fig)

In this example we'll choose a region that looks like it has a several plumes being emitted from the same source, a landfill in Jordan. To create a simple bounding box around our target region, we can just use the plumes that extend furthest in the cardinal directions to generate a bounding box around the region that we can use in our upcoming analysis. 

Create a list of these plumes.

In [9]:
# Note these index values can change if new data is added
plumes =[143,191,235]

Use our list of plumes to index our `GeoDataFrame` (gdf) to create a bounding box enveloping those geometries.

In [10]:
bbox = gdf.loc[plumes].geometry.unary_union.envelope
bbox = orient(bbox, sign=1)
plume_bbox = gpd.GeoDataFrame({"name":['plume_bbox'], "geometry":[bbox]},crs=gdf.crs)
plume_bbox

name                                           geometry
0  plume_bbox  POLYGON ((36.10753 31.80920, 36.28050 31.80920...

Visualize our selected region, plumes, and bounding box.

In [11]:
# Set up Figure and Basemap tiles
fig = Figure(width="1080px",height="540")
map1 = folium.Map(tiles=None)
folium.TileLayer(tiles='https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}',name='Google Satellite', attr='Google', overlay=True).add_to(map1)
folium.TileLayer(tiles='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}.png',
                name='ESRI World Imagery',
                attr='Tiles &copy; Esri &mdash; Source: Esri, i-cubed, USDA, USGS, AEX, GeoEye, Getmapping, Aerogrid, IGN, IGP, UPR-EGP, and the GIS User Community',
                overlay='True').add_to(map1)
fig.add_child(map1)
# Add Search Results gdf
plume_bbox.explore("name",
                   name='Plume BBox',
                   style_kwds={"fillOpacity":0,"width":2},
                   m=map1,
                   legend=False)

gdf.explore("_single_date_time",
            categorical=True,
            style_kwds={"fillOpacity":0.1,"width":2},
            name="EMIT L2B CH4PLM",
            tooltip=[
                "index",
                "native-id",
                "_single_date_time",
            ],
            m=map1,
            legend=False
)
# Zoom to Data
map1.fit_bounds(bounds=convert_bounds(plume_bbox.unary_union.bounds))
# Add Layer controls
map1.add_child(folium.LayerControl(collapsed=False))
display(fig)

We can save our bounding box to a `geojson` file if desired using the cell below.

In [12]:
plume_bbox.to_file(f'{methane_dir}jordan_plumes_bbox.geojson', driver='GeoJSON')

Subset our geodataframe of plumes to only those that intersect our bounding box.

In [13]:
plm_gdf = gdf[gdf.geometry.intersects(plume_bbox.geometry[0])]
plm_gdf

size                                   native-id provider-id  \
66   0.059670  EMIT_L2B_CH4PLM_001_20230217T111603_000653     LPCLOUD   
109  0.006639  EMIT_L2B_CH4PLM_001_20230221T093954_000697     LPCLOUD   
110  0.006958  EMIT_L2B_CH4PLM_001_20230221T093954_000698     LPCLOUD   
143  0.075801  EMIT_L2B_CH4PLM_001_20230225T080543_000746     LPCLOUD   
168  0.006796  EMIT_L2B_CH4PLM_001_20230327T120858_002591     LPCLOUD   
191  0.159388  EMIT_L2B_CH4PLM_001_20230404T085908_000796     LPCLOUD   
235  0.027813  EMIT_L2B_CH4PLM_001_20230420T104534_000833     LPCLOUD   
254  0.029897  EMIT_L2B_CH4PLM_001_20230424T090818_000855     LPCLOUD   
327  0.042873  EMIT_L2B_CH4PLM_001_20230531T102316_000310     LPCLOUD   
495  0.011008  EMIT_L2B_CH4PLM_001_20230627T075201_000054     LPCLOUD   
496  0.008077  EMIT_L2B_CH4PLM_001_20230627T075201_000053     LPCLOUD   
497  0.005943  EMIT_L2B_CH4PLM_001_20230627T075201_000055     LPCLOUD   
723  0.021368  EMIT_L2B_CH4PLM_001_20230926T114143_001755     LPCLOUD   
736  0.037036  EMIT_L2B_CH4PLM_001_20230930T100543_001698     LPCLOUD   
825  0.036863  EMIT_L2B_CH4PLM_001_20231016T114853_001732     LPCLOUD   

        _single_date_time                                      _related_urls  \
66   2023-02-17T11:16:03Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
109  2023-02-21T09:39:54Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
110  2023-02-21T09:39:54Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
143  2023-02-25T08:05:43Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
168  2023-03-27T12:08:58Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
191  2023-04-04T08:59:08Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
235  2023-04-20T10:45:34Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
254  2023-04-24T09:08:18Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
327  2023-05-31T10:23:16Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
495  2023-06-27T07:52:01Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
496  2023-06-27T07:52:01Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
497  2023-06-27T07:52:01Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
723  2023-09-26T11:41:43Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
736  2023-09-30T10:05:43Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
825  2023-10-16T11:48:53Z  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   

                                              geometry  index  
66   POLYGON ((36.17260 31.99519, 36.17097 31.99356...     66  
109  POLYGON ((36.18778 31.93066, 36.18561 31.92904...    109  
110  POLYGON ((36.19862 31.93175, 36.19429 31.92850...    110  
143  POLYGON ((36.18778 31.93121, 36.18561 31.93012...    143  
168  POLYGON ((36.18778 31.93121, 36.18561 31.92850...    168  
191  POLYGON ((36.12813 32.12750, 36.11621 32.12478...    191  
235  POLYGON ((36.26695 31.93609, 36.26044 31.93500...    235  
254  POLYGON ((36.19917 31.92036, 36.19808 31.91331...    254  
327  POLYGON ((36.25339 31.96428, 36.25068 31.96374...    327  
495  POLYGON ((36.22899 31.91331, 36.22519 31.91114...    495  
496  POLYGON ((36.20242 31.92741, 36.19862 31.92578...    496  
497  POLYGON ((36.25014 31.89705, 36.24851 31.89596...    497  
723  POLYGON ((36.18724 31.93392, 36.18344 31.93283...    723  
736  POLYGON ((36.22086 31.93609, 36.21760 31.93121...    736  
825  POLYGON ((36.20025 31.93880, 36.19808 31.93771...    825

If we look at an example of the `_related_urls` column in our geodataframe, we can see it contains the various links to assets associated with that plume.

In [14]:
plm_gdf['_related_urls'].iloc[0]

[{'URL': 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2BCH4PLM.001/EMIT_L2B_CH4PLM_001_20230217T111603_000653/EMIT_L2B_CH4PLM_001_20230217T111603_000653.tif',
  'Description': 'Download EMIT_L2B_CH4PLM_001_20230217T111603_000653.tif',
  'Type': 'GET DATA'},
 {'URL': 's3://lp-prod-protected/EMITL2BCH4PLM.001/EMIT_L2B_CH4PLM_001_20230217T111603_000653/EMIT_L2B_CH4PLM_001_20230217T111603_000653.tif',
  'Description': 'This link provides direct download access via S3 to the granule',
  'Type': 'GET DATA VIA DIRECT ACCESS'},
 {'URL': 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2BCH4PLM.001/EMIT_L2B_CH4PLM_001_20230217T111603_000653/EMIT_L2B_CH4PLMMETA_001_20230217T111603_000653.json',
  'Description': 'Download EMIT_L2B_CH4PLMMETA_001_20230217T111603_000653.json',
  'Type': 'GET DATA'},
 {'URL': 's3://lp-prod-protected/EMITL2BCH4PLM.001/EMIT_L2B_CH4PLM_001_20230217T111603_000653/EMIT_L2B_CH4PLMMETA_001_20230217T111603_000653.json',
  'Descripti

We can write a function to return the asset `URL` for a given asset and row in our dataframe.

In [15]:
def get_asset_url(row,asset, key='Type',value='GET DATA'):
    """
    Retrieve a url from the list of dictionaries for a row in the _related_urls column.
    Asset examples: CH4PLM, CH4PLMMETA, RFL, MASK, RFLUNCERT 
    """
    # Add _ to asset so string matching works
    asset = f"_{asset}_"
    # Retrieve URL matching parameters
    for _dict in row['_related_urls']:
        if _dict.get(key) == value and asset in _dict['URL'].split('/')[-1]:
            return _dict['URL']

Write another function to make a request to retrieve the json metadata for a given plume, using our `get_asset_url` function to select the correct URL from the dataframe.

In [16]:
# Function to fetch CH4 Plume Metadata
# Speed could be improved here by using asyncio/aiohttp
def fetch_ch4_metadata(row):
    response = requests.get(get_asset_url(row, 'CH4PLMMETA'))
    return response.json()['features'][0]['properties']

In [17]:
fetch_ch4_metadata(plm_gdf.iloc[0])

{'Concentration Uncertainty (ppm m)': 472.0,
 'DAAC Scene Numbers': ['012'],
 'DCID': '1360369862',
 'Latitude of max concentration': 31.93635834020197,
 'Longitude of max concentration': 36.185882153048006,
 'Max Plume Concentration (ppm m)': 2989.0,
 'Orbit': '2304807',
 'Plume ID': 'CH4_PlumeComplex-653',
 'Scene FIDs': ['emit20230217t111603'],
 'UTC Time Observed': '2023-02-17T11:16:03Z',
 'map_endtime': '2023-02-17T11:16:04Z',
 'DAAC Scene Names': ['EMIT_L2B_CH4ENH_V001_20230217T111603_2304807_012']}

Retrieve additional plume metadata contained in the EMIT L2B Estimated Methane Plume Complexes (EMITL2BCH4PLM) data product, which contains the maximum enhancement value, the uncertainty of the plume complex, and the list of source scenes.

In [18]:
# Apply the function to each row and convert the result to a DataFrame
plm_meta = plm_gdf.apply(fetch_ch4_metadata, axis=1).apply(pd.Series)

In [19]:
plm_meta

Concentration Uncertainty (ppm m) DAAC Scene Numbers        DCID  \
66                               472.0              [012]  1360369862   
109                              622.0              [016]  1360370029   
110                              411.0              [016]  1360370029   
143                              452.0              [008]  1361045520   
168                              973.0              [041]  1363481211   
191                              351.0              [041]  1364164771   
235                              298.0              [015]  1365875820   
254                              387.0              [012]  1365875987   
327                              290.0              [043]  1368831813   
495                              280.0              [006]  1371320673   
496                              474.0              [006]  1371320673   
497                              270.0              [006]  1371320673   
723                              431.0              [041]  1379181456   
736                              383.0              [041]  1379881634   
825                              360.0              [016]  1380920526   

     Latitude of max concentration  Longitude of max concentration  \
66                       31.936358                       36.185882   
109                      31.926056                       36.189136   
110                      31.924429                       36.199980   
143                      31.924971                       36.195100   
168                      31.928225                       36.191304   
191                      31.938527                       36.182087   
235                      31.928767                       36.223296   
254                      31.912500                       36.201607   
327                      31.946661                       36.231972   
495                      31.907078                       36.235225   
496                      31.922803                       36.209198   
497                      31.895149                       36.251492   
723                      31.929309                       36.195100   
736                      31.925514                       36.196727   
825                      31.928767                       36.215163   

     Max Plume Concentration (ppm m)    Orbit               Plume ID  \
66                            2989.0  2304807   CH4_PlumeComplex-653   
109                           2164.0  2305206   CH4_PlumeComplex-697   
110                           1425.0  2305206   CH4_PlumeComplex-698   
143                           2630.0  2305605   CH4_PlumeComplex-746   
168                           2593.0  2308608  CH4_PlumeComplex-2591   
191                           2169.0  2309406   CH4_PlumeComplex-796   
235                           1427.0  2311007   CH4_PlumeComplex-833   
254                           1679.0  2311406   CH4_PlumeComplex-855   
327                           1481.0  2315107   CH4_PlumeComplex-310   
495                           1261.0  2317805    CH4_PlumeComplex-54   
496                           1916.0  2317805    CH4_PlumeComplex-53   
497                           1096.0  2317805    CH4_PlumeComplex-55   
723                           1954.0  2326908  CH4_PlumeComplex-1755   
736                           2355.0  2327307  CH4_PlumeComplex-1698   
825                           1984.0  2328908  CH4_PlumeComplex-1732   

                Scene FIDs     UTC Time Observed           map_endtime  \
66   [emit20230217t111603]  2023-02-17T11:16:03Z  2023-02-17T11:16:04Z   
109  [emit20230221t093954]  2023-02-21T09:39:54Z  2023-02-21T09:39:55Z   
110  [emit20230221t093954]  2023-02-21T09:39:54Z  2023-02-21T09:39:55Z   
143  [emit20230225t080543]  2023-02-25T08:05:31Z  2023-02-25T08:05:32Z   
168  [emit20230327t120858]  2023-03-27T12:08:46Z  2023-03-27T12:08:47Z   
191  [emit20230404t085908]  2023-04-04T08:58:44Z  2023-04-04T08:58:45Z   
235  [emit20230420t104534]  2023-04-20T10:45

We can add the points with highest methane concentration to our visualization.

Create an index column, as we did for the plumes, then convert the latitude and longitude of max concentration to a shapely `Point` object and add it to our `GeoDataFrame`.

In [20]:
# Specify index so we can reference it with gdf.explore()
plm_meta['index'] = plm_meta.index
# Add Geometry and convert to geodataframe
plm_meta['geometry'] = plm_meta.apply(lambda row: Point(row['Longitude of max concentration'], row['Latitude of max concentration']), axis=1)
plm_meta = gpd.GeoDataFrame(plm_meta, geometry='geometry', crs='EPSG:4326')

In [21]:
plm_meta

Concentration Uncertainty (ppm m) DAAC Scene Numbers        DCID  \
66                               472.0              [012]  1360369862   
109                              622.0              [016]  1360370029   
110                              411.0              [016]  1360370029   
143                              452.0              [008]  1361045520   
168                              973.0              [041]  1363481211   
191                              351.0              [041]  1364164771   
235                              298.0              [015]  1365875820   
254                              387.0              [012]  1365875987   
327                              290.0              [043]  1368831813   
495                              280.0              [006]  1371320673   
496                              474.0              [006]  1371320673   
497                              270.0              [006]  1371320673   
723                              431.0              [041]  1379181456   
736                              383.0              [041]  1379881634   
825                              360.0              [016]  1380920526   

     Latitude of max concentration  Longitude of max concentration  \
66                       31.936358                       36.185882   
109                      31.926056                       36.189136   
110                      31.924429                       36.199980   
143                      31.924971                       36.195100   
168                      31.928225                       36.191304   
191                      31.938527                       36.182087   
235                      31.928767                       36.223296   
254                      31.912500                       36.201607   
327                      31.946661                       36.231972   
495                      31.907078                       36.235225   
496                      31.922803                       36.209198   
497                      31.895149                       36.251492   
723                      31.929309                       36.195100   
736                      31.925514                       36.196727   
825                      31.928767                       36.215163   

     Max Plume Concentration (ppm m)    Orbit               Plume ID  \
66                            2989.0  2304807   CH4_PlumeComplex-653   
109                           2164.0  2305206   CH4_PlumeComplex-697   
110                           1425.0  2305206   CH4_PlumeComplex-698   
143                           2630.0  2305605   CH4_PlumeComplex-746   
168                           2593.0  2308608  CH4_PlumeComplex-2591   
191                           2169.0  2309406   CH4_PlumeComplex-796   
235                           1427.0  2311007   CH4_PlumeComplex-833   
254                           1679.0  2311406   CH4_PlumeComplex-855   
327                           1481.0  2315107   CH4_PlumeComplex-310   
495                           1261.0  2317805    CH4_PlumeComplex-54   
496                           1916.0  2317805    CH4_PlumeComplex-53   
497                           1096.0  2317805    CH4_PlumeComplex-55   
723                           1954.0  2326908  CH4_PlumeComplex-1755   
736                           2355.0  2327307  CH4_PlumeComplex-1698   
825                           1984.0  2328908  CH4_PlumeComplex-1732   

                Scene FIDs     UTC Time Observed           map_endtime  \
66   [emit20230217t111603]  2023-02-17T11:16:03Z  2023-02-17T11:16:04Z   
109  [emit20230221t093954]  2023-02-21T09:39:54Z  2023-02-21T09:39:55Z   
110  [emit20230221t093954]  2023-02-21T09:39:54Z  2023-02-21T09:39:55Z   
143  [emit20230225t080543]  2023-02-25T08:05:31Z  2023-02-25T08:05:32Z   
168  [emit20230327t120858]  2023-03-27T12:08:46Z  2023-03-27T12:08:47Z   
191  [emit20230404t085908]  2023-04-04T08:58:44Z  2023-04-04T08:58:45Z   
235  [emit20230420t104534]  2023-04-20T10:45

Now add this to our visualization.

In [22]:
# Set up Figure and Basemap tiles
fig = Figure(width="1080px",height="540")
map1 = folium.Map(tiles=None)
folium.TileLayer(tiles='https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}',name='Google Satellite', attr='Google', overlay=True).add_to(map1)
folium.TileLayer(tiles='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}.png',
                name='ESRI World Imagery',
                attr='Tiles &copy; Esri &mdash; Source: Esri, i-cubed, USDA, USGS, AEX, GeoEye, Getmapping, Aerogrid, IGN, IGP, UPR-EGP, and the GIS User Community',
                overlay='True').add_to(map1)
fig.add_child(map1)
# Add Search Results gdf
plume_bbox.explore("name",
                   name='Plume BBox',
                   style_kwds={"fillOpacity":0,"width":2},
                   m=map1,
                   legend=False)

plm_gdf.explore("index",
            categorical=True,
            style_kwds={"fillOpacity":0.1,"width":2},
            name="EMIT L2B CH4PLM",
            tooltip=[
                "index",
                "native-id",
                "_single_date_time",
            ],
            m=map1,
            legend=False
)

plm_meta.explore("index",
            categorical=True,
            style_kwds={"fillOpacity":0.1,"width":2},
            name="Location of Max Concentration (ppm m)",
            tooltip=[
                "DAAC Scene Names",
                "UTC Time Observed",
                "Max Plume Concentration (ppm m)",
                "Concentration Uncertainty (ppm m)",
                "Orbit"
            ],
            m=map1,
            legend=False
)
# Zoom to Data
map1.fit_bounds(bounds=convert_bounds(plume_bbox.unary_union.bounds))
# Add Layer controls
map1.add_child(folium.LayerControl(collapsed=False))
display(fig)

## 3. Creating a Timeseries from Plume Data<a id='plume-timeseries'></a>

We can visualize a timeseries of these plumes that appear to be from the same source. To do this we'll generate a list of the COG urls for the plumes, then use rioxarray to stream the data and build a timeseries dataset based on the timestamps in the filenames.

Use the `get_asset_url` function to retrieve the CH4PLM asset URLs by applying it to our dataframe and converting the output to a list.

In [23]:
# Iterate over rows in the plm_gdf and get the CH4PLM urls and store them in a list
plm_urls = plm_gdf.apply(lambda row: get_asset_url(row, asset='CH4PLM'), axis=1).tolist()
plm_urls

['https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2BCH4PLM.001/EMIT_L2B_CH4PLM_001_20230217T111603_000653/EMIT_L2B_CH4PLM_001_20230217T111603_000653.tif',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2BCH4PLM.001/EMIT_L2B_CH4PLM_001_20230221T093954_000697/EMIT_L2B_CH4PLM_001_20230221T093954_000697.tif',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2BCH4PLM.001/EMIT_L2B_CH4PLM_001_20230221T093954_000698/EMIT_L2B_CH4PLM_001_20230221T093954_000698.tif',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2BCH4PLM.001/EMIT_L2B_CH4PLM_001_20230225T080543_000746/EMIT_L2B_CH4PLM_001_20230225T080543_000746.tif',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2BCH4PLM.001/EMIT_L2B_CH4PLM_001_20230327T120858_002591/EMIT_L2B_CH4PLM_001_20230327T120858_002591.tif',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2BCH4PLM.001/EMIT_L2B_CH4PLM_001_20230404T085908_000796/EMIT_

Now that we have a list of COG urls we can set our `gdal` configuration options to pass our NASA Earthdata login credentials when we access each COG.

In [24]:
# GDAL configurations used to successfully access LP DAAC Cloud Assets via vsicurl 
gdal.SetConfigOption('GDAL_HTTP_COOKIEFILE','~/cookies.txt')
gdal.SetConfigOption('GDAL_HTTP_COOKIEJAR', '~/cookies.txt')
gdal.SetConfigOption('GDAL_DISABLE_READDIR_ON_OPEN','EMPTY_DIR')
gdal.SetConfigOption('CPL_VSIL_CURL_ALLOWED_EXTENSIONS','TIF')
gdal.SetConfigOption('GDAL_HTTP_UNSAFESSL', 'YES')

To build our timeseries we will start by opening all the necessary data. Loop over our list of urls, open each plume, merge plumes acquired at the same time, and store them in a dictionary where keys correspond to the acquisition time and values are the plume data in an `xarray.DataArray`.

In [25]:
plm_ts_dict = {}
# Set max retries for vsicurl errors
max_retries=5
# Iterate over plm urls
for url in plm_urls:
    # retrieve acquisition time from url
    acquisition_time = url.split('/')[-1].split('.')[-2].split('_')[-2]
    # list plumes identified in same scene if there are any
    same_scene = [url for url in plm_urls if acquisition_time in url.split('/')[-1].split('.')[-2].split('_')[-2]]
    to_merge = []
    # prevent duplicate processing of plumes from the same scene
    if acquisition_time not in list(plm_ts_dict.keys()):
        # Open and merge plumes identified from each scene
        for _plm in same_scene:
            print(f"Opening {_plm.split('/')[-1]}")
            # Try loop for vsicurl/unrecongnized format error
            for retry in range(max_retries):
                try:
                    # Open COG and squeeze band dimension
                    plm = rxr.open_rasterio(_plm).squeeze('band', drop=True)
                    break
                except Exception as e:
                    print(f'{e} Retrying...')
                else:
                    print(f"Failed to process {url} after {max_retries} retries. Please check to see you're authenticated with earthaccess.")
            # Add to list of plumes to merge
            to_merge.append(plm)
            # Merge plumes and add to timeseries
            plm_ts_dict[acquisition_time] = rxr.merge.merge_arrays(to_merge)    

Opening EMIT_L2B_CH4PLM_001_20230217T111603_000653.tif
Opening EMIT_L2B_CH4PLM_001_20230221T093954_000697.tif
Opening EMIT_L2B_CH4PLM_001_20230221T093954_000698.tif
Opening EMIT_L2B_CH4PLM_001_20230225T080543_000746.tif
Opening EMIT_L2B_CH4PLM_001_20230327T120858_002591.tif
Opening EMIT_L2B_CH4PLM_001_20230404T085908_000796.tif
Opening EMIT_L2B_CH4PLM_001_20230420T104534_000833.tif
Opening EMIT_L2B_CH4PLM_001_20230424T090818_000855.tif
Opening EMIT_L2B_CH4PLM_001_20230531T102316_000310.tif
Opening EMIT_L2B_CH4PLM_001_20230627T075201_000054.tif
Opening EMIT_L2B_CH4PLM_001_20230627T075201_000053.tif
Opening EMIT_L2B_CH4PLM_001_20230627T075201_000055.tif
Opening EMIT_L2B_CH4PLM_001_20230926T114143_001755.tif
Opening EMIT_L2B_CH4PLM_001_20230930T100543_001698.tif
Opening EMIT_L2B_CH4PLM_001_20231016T114853_001732.tif


Now that we have a plume object for each date in our timeseries, we need to put them all on a common grid so they are spatially aligned before we can stack them along the time dimension.

To do this, we will find the minimum and maximum bounds of each dataarray in our dictionary, then create a common grid to reproject to.

In [26]:
from typing import List
def create_common_grid(data_arrays: List[xr.DataArray]) -> xr.DataArray:
    """
    Create a common grid for a list of xarray DataArrays, matching the resolution of the first data array.
    """
    # Initial Bounds for common grid
    minx = miny = float('inf')
    maxx = maxy = float('-inf')

    for array in data_arrays:
        left, bottom, right, top = array.rio.bounds()
        minx = min(minx, left)
        miny = min(miny, bottom)
        maxx = max(maxx, right)
        maxy = max(maxy, top)

    bounds = (minx, miny, maxx, maxy)

    res = data_arrays[0].rio.resolution()
    crs = data_arrays[0].rio.crs
    nodata = data_arrays[0].rio.nodata

    # # Calculate new raster shape using the new extent, maintaining the original resolution
    height = int(np.ceil((bounds[3] - bounds[1]) / abs(res[1])))
    width = int(np.ceil((bounds[2] - bounds[0]) / abs(res[0])))
    data = np.full((height,width),nodata)
    coords = {'y':(['y'],np.arange(bounds[1], bounds[3], abs(res[1]))),
              'x':(['x'],np.arange(bounds[0], bounds[2], abs(res[0])))}
    common_grid = xr.DataArray(data, coords=coords)
    common_grid.rio.write_crs(crs, inplace=True)
    return(common_grid)

In [27]:
common_grid = create_common_grid(list(plm_ts_dict.values()))
common_grid

<xarray.DataArray (y: 586, x: 319)>
array([[-9999., -9999., -9999., ..., -9999., -9999., -9999.],
       [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
       [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
       ...,
       [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
       [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
       [-9999., -9999., -9999., ..., -9999., -9999., -9999.]],
      dtype=float32)
Coordinates:
  * y            (y) float64 31.81 31.81 31.81 31.81 ... 32.13 32.13 32.13 32.13
  * x            (x) float64 36.11 36.11 36.11 36.11 ... 36.28 36.28 36.28 36.28
    spatial_ref  int64 0

Reproject each of the plume dataarrays to the common grid.

In [28]:
plm_ts_dict = {key: value.rio.reproject_match(common_grid) for key, value in plm_ts_dict.items()}

Now that we have all of our plumes on a standard grid, we can concatenate them along a time dimension to create a timeseries. Create an xarray variable called 'time' from our dictionary keys, then use `xarray.concat` to concatenate all of our plumes along the time dimension.

In [29]:
plm_time = xr.Variable('time', [datetime.strptime(t,'%Y%m%dT%H%M%S') for t in list(plm_ts_dict.keys())])
plm_time

<xarray.Variable (time: 12)>
array(['2023-02-17T11:16:03.000000000', '2023-02-21T09:39:54.000000000',
       '2023-02-25T08:05:43.000000000', '2023-03-27T12:08:58.000000000',
       '2023-04-04T08:59:08.000000000', '2023-04-20T10:45:34.000000000',
       '2023-04-24T09:08:18.000000000', '2023-05-31T10:23:16.000000000',
       '2023-06-27T07:52:01.000000000', '2023-09-26T11:41:43.000000000',
       '2023-09-30T10:05:43.000000000', '2023-10-16T11:48:53.000000000'],
      dtype='datetime64[ns]')

In [30]:
plm_ts_ds = xr.concat(list(plm_ts_dict.values()), dim=plm_time)
plm_ts_ds

<xarray.DataArray (time: 12, y: 586, x: 319)>
array([[[-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        ...,
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.]],

       [[-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        ...,
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.]],

       [[-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        ...,
...
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.]],

       [[-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        ...,
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.]],

       [[-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        ...,
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.],
        [-9999., -9999., -9999., ..., -9999., -9999., -9999.]]],
      dtype=float32)
Coordinates:
    spatial_ref  int64 0
  * x            (x) float64 36.11 36.11 36.11 36.11 ... 36.28 36.28 36.28 36.28
  * y            (y) float64 31.81 31.81 31.81 31.81 ... 32.13 32.13 32.13 32.13
  * time         (time) datetime64[ns] 2023-02-17T11:16:03 ... 2023-10-16T11:...
Attributes: (12/34)
    AREA_OR_POINT:                     Area
    Conventions:                       CF-1.63
    creator_name:                      Jet Propulsion Laboratory/California I...
    creator_url:                       https://earth.jpl.nasa.gov/emit/
    date_created:                      2023-09-25T18:53:09Z
    Estimated_Uncertainty_ppmm:        472.0
    ...                                ...
    title:                             EMIT
    Units:                             ppm m
    UTC_Time_Observed:                 2023-02-17T11:16:03Z
    scale_factor:                      1.0
    add_offset:                        0.0
    _FillValue:                        -9999.0

Set our no_data values to `np.nan` to make sure they are transparent for improved visualization.

In [31]:
plm_ts_ds.data[plm_ts_ds.data == -9999] = np.nan

Plot the plume time series.

In [32]:
plm_ts_plot = plm_ts_ds.hvplot.image(x='x',y='y',geo=True, tiles='ESRI', crs='EPGS:4326', cmap='inferno',clim=(0,np.nanmax(plm_ts_ds.data)),clabel=f'Methane Concentation ({plm_ts_ds.Units})', frame_width=600, frame_height=600, rasterize=True)

In [33]:
plm_ts_plot

:DynamicMap   [time]
   :Overlay
      .WMTS.I  :WMTS   [Longitude,Latitude]
      .Image.I :Image   [x,y]   (value)

## 4. Calculating the IME for each plume<a id='ime'></a>

The integrated mass enhancement (IME), a sum of the mass of methane present in each plume is calculated by summing the mass of methane present in all plume pixels. The IME in kilograms (kg) can be estimated by using the equation below which includes the mixing ratio length per pixel (ppmm), the area of the pixel (m^2), where 22.4 is the volume of 1 mole of gas at standard temperature and pressure (STP) in liters, and 0.01604 is the molar mass of methane in kg/mol.

The IME can be combined with a plume length and windspeed to estimate emissions in units of kg per hour, but in this tutorial, we will not calculate emissions, rather keep things simple and calculate the IME for each plume and observe how these values change over time.

$$\ kg\ \ (per \ \ pixel) = \frac{pixel \ \ value \ \ ppm \cdot m}{1} \frac{1}{1 \cdot 10^6 \ \ ppm} \frac {60 \ \ m \cdot 60 \ \ m} {1} \frac {1000 \ \ L} {m^3} \frac {1 \ \ mol} {22.4 \ \ L} \frac {0.01604 \ \ kg} {1 \ \ mol}$$

We can write this as a function for each pixel, then apply it to the entire timeseries to calculate the IME for each plume.

In [34]:
def calc_ime(plume_da):
    molar_volume = 22.4 # L/mol at STP
    molar_mass_ch4 = 0.01604 #kg/mol

    kg = plume_da * (1/1e6) * (60*60) * (1000) * (1/molar_volume) * molar_mass_ch4
    ime = np.nansum(kg)
    return ime

In [35]:
# Apply the function along the 'x' and 'y' dimensions
ime_ts = xr.apply_ufunc(calc_ime, plm_ts_ds, input_core_dims=[['y', 'x']], vectorize=True)
ime_ts.name = 'value'

In [36]:
ime_plot = ime_ts.hvplot.scatter(x='time',y='value', title='Observed Integrated Methane Emissions (kg) over 2023', color='black', xticks=list(ime_ts.time.data), rot=90, grid=True, xlabel='Date Observed', ylabel='IME (kg)')

In [37]:
ime_plot

:Scatter   [time]   (value)

## 5. Further investigation into plume detection<a id='plume-detection'></a>

The timeseries shown above doesn't necessarily give us a full a full picture methane emissions at the landfill. In addition to cases where no emissions were observed, gaps in data can result from absence of observations due the variable revisit period of the ISS, or clouds. To add more context to this plume timeseries, we will look at all EMIT acquisitions over the target regions and try to determine if there were factors affecting plume detection, or simply no methane emissions during those for any other overpass.

For this search we'll want to restrict our search to a smaller ROI than our bounding box. We want to pick something smaller more centered around the source of the emission, so we avoid retrieving irrelevant data, for example an overpass barely crossing the corner of our large bounding box. To do this we will use the maximum concentration points from our plumes to create a smaller ROI that is likely to include a methane plume if one is present.

Create a new polygon using the maximum concentration points from our plumes as vertices, then orienting the points in counter-clockwise order so they are compatible with an `earthaccess` search. This is just a simple example approach, there are several ways we could define a smaller ROI using the plume data or ancillary information.

In [38]:
max_conc_poly = plm_meta.geometry.unary_union.envelope
max_conc_poly = orient(max_conc_poly, sign=1.0)
max_conc_gdf = gpd.GeoDataFrame({"name":['max_points'], "geometry":[max_conc_poly]},crs=plm_meta.crs)

In [39]:
roi = list(max_conc_gdf.geometry[0].exterior.coords)
roi

[(36.18208652540615, 31.895148668662497),
 (36.251492287998964, 31.895148668662497),
 (36.251492287998964, 31.946660758086832),
 (36.18208652540615, 31.946660758086832),
 (36.18208652540615, 31.895148668662497)]

Now conduct a search for reflectance data over our ROI and convert the results to a `geopandas.GeoDataFrame`.

In [40]:
rfl_results = earthaccess.search_data(
    concept_id=concept_ids['reflectance'],
    polygon=roi,
    temporal= date_range, #('2023-03-01','2023-03-31')
    count=2000
)
rfl_gdf = results_to_geopandas(rfl_results)
rfl_gdf

Granules found: 20


size                                     native-id provider-id  \
0   3577.229322  EMIT_L2A_RFL_001_20230201T093205_2303207_042     LPCLOUD   
1   3578.123960  EMIT_L2A_RFL_001_20230201T093216_2303207_043     LPCLOUD   
2   3579.567969  EMIT_L2A_RFL_001_20230205T075526_2303606_032     LPCLOUD   
3   3580.065893  EMIT_L2A_RFL_001_20230217T111603_2304807_012     LPCLOUD   
4   3580.397926  EMIT_L2A_RFL_001_20230221T093954_2305206_016     LPCLOUD   
5   3579.428516  EMIT_L2A_RFL_001_20230225T080543_2305605_008     LPCLOUD   
6   3581.146609  EMIT_L2A_RFL_001_20230327T120858_2308608_041     LPCLOUD   
7   3580.950398  EMIT_L2A_RFL_001_20230327T120910_2308608_042     LPCLOUD   
8   3576.435364  EMIT_L2A_RFL_001_20230331T103323_2309007_041     LPCLOUD   
9   3579.713533  EMIT_L2A_RFL_001_20230404T085908_2309406_041     LPCLOUD   
10  3579.956654  EMIT_L2A_RFL_001_20230420T104534_2311007_015     LPCLOUD   
11  3580.076920  EMIT_L2A_RFL_001_20230424T090818_2311406_012     LPCLOUD   
12  3579.732953  EMIT_L2A_RFL_001_20230531T102316_2315107_043     LPCLOUD   
13  3579.619687  EMIT_L2A_RFL_001_20230531T102328_2315107_044     LPCLOUD   
14  3580.033607  EMIT_L2A_RFL_001_20230627T075201_2317805_006     LPCLOUD   
15  3580.056995  EMIT_L2A_RFL_001_20230926T114143_2326908_041     LPCLOUD   
16  3579.252819  EMIT_L2A_RFL_001_20230930T100543_2327307_041     LPCLOUD   
17  3579.484532  EMIT_L2A_RFL_001_20230930T100555_2327307_042     LPCLOUD   
18  3578.353755  EMIT_L2A_RFL_001_20231016T114853_2328908_016     LPCLOUD   
19  3579.505513  EMIT_L2A_RFL_001_20231220T100611_2335407_005     LPCLOUD   

    _beginning_date_time     _ending_date_time  \
0   2023-02-01T09:32:05Z  2023-02-01T09:32:16Z   
1   2023-02-01T09:32:16Z  2023-02-01T09:32:28Z   
2   2023-02-05T07:55:26Z  2023-02-05T07:55:38Z   
3   2023-02-17T11:16:03Z  2023-02-17T11:16:14Z   
4   2023-02-21T09:39:54Z  2023-02-21T09:40:06Z   
5   2023-02-25T08:05:43Z  2023-02-25T08:05:55Z   
6   2023-03-27T12:08:58Z  2023-03-27T12:09:10Z   
7   2023-03-27T12:09:10Z  2023-03-27T12:09:21Z   
8   2023-03-31T10:33:23Z  2023-03-31T10:33:35Z   
9   2023-04-04T08:59:08Z  2023-04-04T08:59:20Z   
10  2023-04-20T10:45:34Z  2023-04-20T10:45:46Z   
11  2023-04-24T09:08:18Z  2023-04-24T09:08:29Z   
12  2023-05-31T10:23:16Z  2023-05-31T10:23:28Z   
13  2023-05-31T10:23:28Z  2023-05-31T10:23:40Z   
14  2023-06-27T07:52:01Z  2023-06-27T07:52:13Z   
15  2023-09-26T11:41:43Z  2023-09-26T11:41:55Z   
16  2023-09-30T10:05:43Z  2023-09-30T10:05:55Z   
17  2023-09-30T10:05:55Z  2023-09-30T10:06:06Z   
18  2023-10-16T11:48:53Z  2023-10-16T11:49:05Z   
19  2023-12-20T10:06:11Z  2023-12-20T10:06:23Z   

                                        _related_urls  \
0   [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
1   [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
2   [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
3   [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
4   [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
5   [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
6   [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
7   [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
8   [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
9   [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
10  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
11  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
12  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
13  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
14  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
15  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
16  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
17  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
18  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   
19  [{'URL': 'https://data.lpdaac.earthdatacloud.n...   

                                             geometry  
0   POLYGON ((35.92897 32.38961, 35.22028 31.76677...  
1   POLYGON ((36.55009 32.91588,

From the results we can see we have 20 scenes that intersect our ROI. We can visualize the footprints of these scenes to gain some insight into coverage over our ROI. 

In [41]:
# Set up Figure and Basemap tiles
fig = Figure(width="1080px",height="540")
map1 = folium.Map(tiles=None)
folium.TileLayer(tiles='https://mt1.google.com/vt/lyrs=y&x={x}&y={y}&z={z}',name='Google Satellite', attr='Google', overlay=True).add_to(map1)
folium.TileLayer(tiles='https://server.arcgisonline.com/ArcGIS/rest/services/World_Imagery/MapServer/tile/{z}/{y}/{x}.png',
                name='ESRI World Imagery',
                attr='Tiles &copy; Esri &mdash; Source: Esri, i-cubed, USDA, USGS, AEX, GeoEye, Getmapping, Aerogrid, IGN, IGP, UPR-EGP, and the GIS User Community',
                overlay='True').add_to(map1)
fig.add_child(map1)

# Add Search Reflectance Scenes with no CH4
rfl_gdf.explore(color='red',
               style_kwds={"fillOpacity":0,"width":2},
               name="Scenes with no CH4 Plumes",
               tooltip=[
                "native-id",
                "_beginning_date_time",
                ],
                m=map1,
                legend=False)

# Add Plume BBox to Map
max_conc_gdf.explore(m=map1,
                   name='Plumes Bounding Box',
                   legend=False)

# Zoom to Data
map1.fit_bounds(bounds=convert_bounds(rfl_gdf.unary_union.bounds))
# Add Layer controls
map1.add_child(folium.LayerControl(collapsed=False))
display(fig)

From this we can see that there are several scenes that intersect with our ROI, but likely have no relevant information since they only cover a small portion or corner of the ROI.

We can use a similar process as with the methane product to construct a time series to better understand the data gathered on each overpass. To do this, we will use the browse imagery and the masks included in the EMITL2ARFL product. The by default the mask files and browse images are not orthorectified, so we must do that as part of our workflow.

First, get the urls for the browse images and masks for each scene in our `rfl_gdf` search results using the `get_asset_urls` function.

In [42]:
png_urls = rfl_gdf.apply(lambda row: get_asset_url(row, asset='RFL', value='GET RELATED VISUALIZATION'), axis=1).tolist()
png_urls

['https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-public/EMITL2ARFL.001/EMIT_L2A_RFL_001_20230201T093205_2303207_042/EMIT_L2A_RFL_001_20230201T093205_2303207_042.png',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-public/EMITL2ARFL.001/EMIT_L2A_RFL_001_20230201T093216_2303207_043/EMIT_L2A_RFL_001_20230201T093216_2303207_043.png',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-public/EMITL2ARFL.001/EMIT_L2A_RFL_001_20230205T075526_2303606_032/EMIT_L2A_RFL_001_20230205T075526_2303606_032.png',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-public/EMITL2ARFL.001/EMIT_L2A_RFL_001_20230217T111603_2304807_012/EMIT_L2A_RFL_001_20230217T111603_2304807_012.png',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-public/EMITL2ARFL.001/EMIT_L2A_RFL_001_20230221T093954_2305206_016/EMIT_L2A_RFL_001_20230221T093954_2305206_016.png',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-public/EMITL2ARFL.001/EMIT_L2A_RFL_001_20230225T080543_2305605_008/EMIT_L2A_RFL_001_20

In [43]:
mask_urls = rfl_gdf.apply(lambda row: get_asset_url(row, asset='MASK'), axis=1).tolist()
mask_urls

['https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2ARFL.001/EMIT_L2A_RFL_001_20230201T093205_2303207_042/EMIT_L2A_MASK_001_20230201T093205_2303207_042.nc',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2ARFL.001/EMIT_L2A_RFL_001_20230201T093216_2303207_043/EMIT_L2A_MASK_001_20230201T093216_2303207_043.nc',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2ARFL.001/EMIT_L2A_RFL_001_20230205T075526_2303606_032/EMIT_L2A_MASK_001_20230205T075526_2303606_032.nc',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2ARFL.001/EMIT_L2A_RFL_001_20230217T111603_2304807_012/EMIT_L2A_MASK_001_20230217T111603_2304807_012.nc',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2ARFL.001/EMIT_L2A_RFL_001_20230221T093954_2305206_016/EMIT_L2A_MASK_001_20230221T093954_2305206_016.nc',
 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/EMITL2ARFL.001/EMIT_L2A_RFL_001_20230225T080543_2305605_008/E

We can write these as a text file so we don't need to search again, although we will use the `rfl_gdf` GeoDataFrame later in the tutorial. 

In [44]:
# # Save URL List
# with open(f'{methane_dir}rfl_mask_urls.txt', 'w') as f:
#     for line in mask_urls:
#         f.write(f"{line}\n")

Since the mask files are not chunked, its quicker to download them to do the processing.

Login with `earthaccess` and download these files.

In [ ]:
earthaccess.login(persist=True)
# Get requests https Session using Earthdata Login Info
fs = earthaccess.get_requests_https_session()
# Retrieve granule asset ID from URL (to maintain existing naming convention)
for url in mask_urls:
    granule_asset_id = url.split('/')[-1]
    # Define Local Filepath
    fp = f'{methane_dir}{granule_asset_id}'
    # Download the Granule Asset if it doesn't exist
    if not os.path.isfile(fp):
        with fs.get(url,stream=True) as src:
            with open(fp,'wb') as dst:
                for chunk in src.iter_content(chunk_size=64*1024*1024):
                    dst.write(chunk)

For each of these scenes we want to open EMIT L2A Mask data, then subset spatially and select only the variable we want, in this case we'll use the `Aggregate flag` from the `masks` dataarray. The `Aggregate flag` includes the cloud mask, dilated cloud mask, cirrus mask, water mask, and an AOD threshold of 0.5. We can assume most of these will affect the methane plume detection.

As we do this, we will also take the GLT, read in the browse image, clip, and orthorectify it to our ROI. We can do this because the browse png files are in the native resolution and can be broadcast onto an orthorectified grid using the GLT.

First, get the filepaths for our downloaded mask data.

In [ ]:
# List the downloaded files
fps = glob.glob(f'{methane_dir}*.nc')
fns = [os.path.basename(fp) for fp in fps]
fns

Create a function to loop through our files, orthorectifying the mask and browse image, clipping and reprojecting to our predefined `common_grid`, and finally saving outputs as a COG.

In [ ]:
def process_scenes(fns, outdir, common_grid):
    """
    This function will process a list of EMIT Mask scenes, downloading, merging adjacent scenes and building a timeseries, as well as orthorectifying/m and returning the browse images.
    """
    for fn in fns:
        # Get Granule Asset ID for First Adjacent Scene (may only be one)
        granule_asset_id = fn.split('.')[-2]
        # Set Output Path
        outpath_mask = f"{outdir}{granule_asset_id}_cloud_flag.tif"
        outpath_browse = f"{outdir}{granule_asset_id}_ortho_browse.tif"
        # Check if the file exists
        if not os.path.isfile(outpath_mask):
            # Open Mask Dataset
            emit_ds = emit_xarray(f'{methane_dir}{fn}', ortho=False)
            # Retrieve GLT, spatial_ref, and geotransform to use on browse image
            glt = np.nan_to_num(np.stack([emit_ds["glt_x"].data, emit_ds["glt_y"].data], axis=-1),nan=0).astype(int)
            spatial_ref = emit_ds.spatial_ref
            gt = emit_ds.geotransform
            # Select browse image url corresponding to the scene
            png_url = [url for url in png_urls if fn.split('.')[-2].split('_')[-3] in url][0]
            # Orthorectify browse and mask
            rgb = ortho_browse(png_url, glt, spatial_ref, gt, white_background=True)
            emit_ds = ortho_xr(emit_ds)
            # Clip to Geometry using rioxarray
            #emit_ds = emit_ds.rio.clip_box(*common_grid.rio.bounds(),common_grid.rio.crs())          
            #rgb = rgb.rio.clip_box(*common_grid.rio.bounds(),common_grid.rio.crs())
            # Select only mask array and desired quality flag and reproject to match our chosen extent
            mask_da = emit_ds['mask'].sel(mask_bands='Cloud flag')
            # Drop elevation
            mask_da = mask_da.drop_vars('elev')
            mask_da.name = 'Cloud flag'
            mask_da.data = np.nan_to_num(mask_da.data, nan=-9999)
            mask_da = mask_da.rio.reproject_match(common_grid, nodata=-9999)
            #mask_da.rio.write_nodata(np.nan, inplace=True)
            # Reproject rgb
            rgb = rgb.rio.reproject_match(common_grid, nodata=255) # 255 for white background
            # Write cog outputs        
            mask_da.rio.to_raster(outpath_mask,driver="COG")
            rgb.rio.to_raster(outpath_browse,driver="COG")

Run the function.

In [ ]:
process_scenes(fns, methane_dir, common_grid)

Create a list of the processed files to use in creation of a timeseries. We'll use a similar process to what we did for the plumes, adding a `time` variable to our datasets and concatenating.

In [ ]:
mask_files = sorted(glob.glob(f'{methane_dir}*cloud_flag.tif'))
mask_files

In [ ]:
rgb_files = sorted(glob.glob(f'{methane_dir}*ortho_browse.tif'))
rgb_files

Build a time index from the filenames.

In [ ]:
def time_index_from_filenames(file_names,datetime_pos):
    """
    Helper function to create a pandas DatetimeIndex
    """
    return [datetime.strptime(f.split('_')[datetime_pos], '%Y%m%dT%H%M%S') for f in file_names]

In [ ]:
mask_time = xr.Variable('time', time_index_from_filenames(mask_files, -5))

Open and concatenate our datasets along the time dimension, then assign fill_values to `np.nan` to make those sections of the data transparent in our visualization.

In [ ]:
quality_ts_da = xr.concat([rxr.open_rasterio(f).squeeze('band', drop=True).rio.reproject_match(common_grid) for f in mask_files], dim=mask_time)

Now, add a column to our plume geodataframe containing a time index formatted similarly to our quality `time` dimension so we can visualize our plume polygons with our quality data.

In [ ]:
plm_gdf['time'] = pd.to_datetime(plm_gdf.loc[:,'_single_date_time'])

Plot the quality timeseries, bounding box, and plume extents on the same figure.

In [ ]:
quality_ts_da.data[quality_ts_da.data < 1] = np.nan
quality_ts_map = quality_ts_da.hvplot.image(x='x',y='y',cmap='greys',groupby='time',clim=(0,1),geo=True,frame_height=400)


RGB images are a good way to add something more visually understandable than just the mask layers. Follow the same process as above to build an RGB timeseries, then plot it with the bounding box and plume extents.

In [ ]:
rgb_ts_ds = xr.concat([rxr.open_rasterio(f).rio.reproject_match(common_grid) for f in rgb_files], dim=mask_time)
rgb_ts_ds.data[rgb_ts_ds.data == -1] = 255

In [ ]:
rgb_ts_map = rgb_ts_ds.hvplot.rgb(x='x',y='y', bands='band',groupby='time',geo=True, frame_height=400, crs='EPSG:4326')

Because we've set our RGB to display as white where there is no data, and our cloud mask where no clouds are present as transparent, we can identify any areas with no data over our ROI by white/transparent, and cloudy areas as black. The larger black lines/rectangles are representative of onboard cloud masking, where no data was downlinked due to a high volume of clouds detected.

In [ ]:
rgb_ts_map*quality_ts_map*plm_gdf.hvplot(groupby='time', geo=True, line_color='red', fill_color=None)*max_conc_gdf.hvplot(color='red',crs='EPSG:4326',fill_color=None, line_color='yellow')

With this information, we can build a dataframe assigning a category to each of the dates where there was no plume detected and add this information to our IME timeseries figure.

Create a dataframe of dates where no plume was detected by finding the dates where there are no plumes in our `mask_time` arrays by removing timestamps from our `plm_time` array.

In [ ]:
no_plm_time = np.setdiff1d(mask_time.data,plm_time.data)
no_plm_time

Build a dataframe out of these dates where there were no plumes detected

In [ ]:
# Build a dataframe
no_plm_df = pd.DataFrame({'time':no_plm_time})
no_plm_df

Next, categorize them based on the visualizations we made and remove any times where there wasn't a good observation of our area of interest.

In [ ]:
# add a category column to describe the observation 
no_plm_df['category'] = 'no_data'
no_plm_df.loc[[0,4],'category'] = 'cloud'
no_plm_df.loc[7,'category'] = 'no_plume'

In [ ]:
no_plm_df = no_plm_df[~no_plm_df['category'].str.contains('no_data')]
no_plm_df['time'] = pd.to_datetime(no_plm_df['time'])
no_plm_df.reset_index(drop=True, inplace=True)
no_plm_df

We can now merge our IME timeseries dataframe with this one, along the time column to add these observations with different categories to our timeseries.

In [ ]:
ime_df = pd.merge(ime_ts.to_dataframe(), no_plm_df, on=['time'], how='outer')
ime_df = ime_df.sort_values(by='time')
ime_df['category']=ime_df['category'].fillna('plume')
ime_df['value'] = ime_df['value'].fillna(0)

In [ ]:
ime_df

We can now plot this IME timeseries alongside our plume timeseries. 

In [ ]:
ime_timeline = ime_df.hvplot.scatter(x='time',y='value', by='category', size=100, xlabel='Date Observed', ylabel='IME (kg)', title='Integrated Methane Emissions (kg) over 2023', rot=90,
                                     grid=True, frame_height=400, frame_width=800, ylim=(0,11000),xticks=list(ime_df.time))

In [ ]:
ime_timeline.opts(legend_position='bottom') + plm_ts_plot.opts(title='Methane Plumes Observed', frame_height=400, frame_width=400)

## Contact Info:
Email: LPDAAC@usgs.gov  
Voice: +1-866-573-3222  
Organization: Land Processes Distributed Active Archive Center (LP DAAC)¹  
Website: https://lpdaac.usgs.gov/  
Date last modified: 03-13-2024  

¹Work performed under USGS contract G15PD00467 for NASA contract NNG14HH33I.  